# Importing Library

In [57]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import os
import matplotlib.pyplot as plt#visualization
from PIL import Image
%matplotlib inline
import pandas as pd
import seaborn as sns#visualization
import itertools
import warnings
warnings.filterwarnings("ignore")
import io
import plotly.offline as py #visualization
py.init_notebook_mode(connected=True) #visualization
import plotly.graph_objs as go #visualization
import plotly.tools as tls #visualization
import plotly.figure_factory as ff #visualization

# Read and Clean Dataset

In [58]:
df = pd.read_csv('bank.csv')
df.head(10)

age         job   marital  education default  balance housing loan  \
0   59      admin.   married  secondary      no     2343     yes   no   
1   56      admin.   married  secondary      no       45      no   no   
2   41  technician   married  secondary      no     1270     yes   no   
3   55    services   married  secondary      no     2476     yes   no   
4   54      admin.   married   tertiary      no      184      no   no   
5   42  management    single   tertiary      no        0     yes  yes   
6   56  management   married   tertiary      no      830     yes  yes   
7   60     retired  divorced  secondary      no      545     yes   no   
8   37  technician   married  secondary      no        1     yes   no   
9   28    services    single  secondary      no     5090     yes   no   

   contact  day month  duration  campaign  pdays  previous poutcome deposit  
0  unknown    5   may      1042         1     -1         0  unknown     yes  
1  unknown    5   may      1467         1     -1         0  unknown     yes  
2  unknown    5   may      1389         1     -1         0  unknown     yes  
3  unknown    5   may       579         1     -1         0  unknown     yes  
4  unknown    5   may       673         2     -1         0  unknown     yes  
5  unknown    5   may       562         2     -1         0  unknown     yes  
6  unknown    6   may      1201         1     -1         0  unknown     yes  
7  unknown    6   may      1030         1     -1         0  unknown     yes  
8  unknown    6   may       608         1     -1         0  unknown     yes  
9  unknown    6   may      1297         3     -1         0  unknown     yes

In [59]:
def overall(df):
    print ("Rows : " ,df.shape[0])
    print ("Columns : " ,df.shape[1])
    print ("\nFeatures : \n" ,df.columns.tolist())
    print ("\nMissing values : ", df.isnull().sum().values.sum())
    print ("\nUnique values : \n", df.nunique())

overall(df)

Rows :  11162
Columns :  17

Features : 
 ['age', 'job', 'marital', 'education', 'default', 'balance', 'housing', 'loan', 'contact', 'day', 'month', 'duration', 'campaign', 'pdays', 'previous', 'poutcome', 'deposit']

Missing values :  0

Unique values : 
 age            76
job            12
marital         3
education       4
default         2
balance      3805
housing         2
loan            2
contact         3
day            31
month          12
duration     1428
campaign       36
pdays         472
previous       34
poutcome        4
deposit         2
dtype: int64


In [60]:
df.describe()

age       balance           day      duration      campaign  \
count  11162.000000  11162.000000  11162.000000  11162.000000  11162.000000   
mean      41.231948   1528.538524     15.658036    371.993818      2.508421   
std       11.913369   3225.413326      8.420740    347.128386      2.722077   
min       18.000000  -6847.000000      1.000000      2.000000      1.000000   
25%       32.000000    122.000000      8.000000    138.000000      1.000000   
50%       39.000000    550.000000     15.000000    255.000000      2.000000   
75%       49.000000   1708.000000     22.000000    496.000000      3.000000   
max       95.000000  81204.000000     31.000000   3881.000000     63.000000   

              pdays      previous  
count  11162.000000  11162.000000  
mean      51.330407      0.832557  
std      108.758282      2.292007  
min       -1.000000      0.000000  
25%       -1.000000      0.000000  
50%       -1.000000      0.000000  
75%       20.750000      1.000000  
max      854.000000     58.000000

In [61]:
#Check null and duplicated variables
def checking(data):
    print("Null-variables: ", df.isnull().sum())
    print('Duplicared variable: ', df.duplicated().sum())
checking(df)

Null-variables:  age          0
job          0
marital      0
education    0
default      0
balance      0
housing      0
loan         0
contact      0
day          0
month        0
duration     0
campaign     0
pdays        0
previous     0
poutcome     0
deposit      0
dtype: int64
Duplicared variable:  0


In [62]:
#Through testing, there are no missing data points and no duplicated data.
df.isna().sum()
df = df.dropna()
df.head()

age         job  marital  education default  balance housing loan  contact  \
0   59      admin.  married  secondary      no     2343     yes   no  unknown   
1   56      admin.  married  secondary      no       45      no   no  unknown   
2   41  technician  married  secondary      no     1270     yes   no  unknown   
3   55    services  married  secondary      no     2476     yes   no  unknown   
4   54      admin.  married   tertiary      no      184      no   no  unknown   

   day month  duration  campaign  pdays  previous poutcome deposit  
0    5   may      1042         1     -1         0  unknown     yes  
1    5   may      1467         1     -1         0  unknown     yes  
2    5   may      1389         1     -1         0  unknown     yes  
3    5   may       579         1     -1         0  unknown     yes  
4    5   may       673         2     -1         0  unknown     yes

# Data Manipulation

In [63]:
df.job.value_counts()

job
management       2566
blue-collar      1944
technician       1823
admin.           1334
services          923
retired           778
self-employed     405
student           360
unemployed        357
entrepreneur      328
housemaid         274
unknown            70
Name: count, dtype: int64

In [64]:
#Remove unknown values from "job" column
df = df[df['job'] != 'unknown']


In [65]:
#Remove special characters from "job" column
df.job = df.job.str.replace(".", "")

In [66]:
#Separating deposit and non deposit customers
deposit = df[df["deposit"] == "yes"]
not_deposit = df[df["deposit"] == "no"]

In [67]:
#Separating catagorical and numerical columns
Id_col = ['']
target_col = ["deposit"]
cat_cols = df.nunique()[df.nunique() < 6].keys().tolist()
cat_cols = [x for x in cat_cols if x not in target_col]
num_cols = [x for x in df.columns if (x not in cat_cols + target_col + Id_col)]

In [68]:
df.head()

age         job  marital  education default  balance housing loan  contact  \
0   59       admin  married  secondary      no     2343     yes   no  unknown   
1   56       admin  married  secondary      no       45      no   no  unknown   
2   41  technician  married  secondary      no     1270     yes   no  unknown   
3   55    services  married  secondary      no     2476     yes   no  unknown   
4   54       admin  married   tertiary      no      184      no   no  unknown   

   day month  duration  campaign  pdays  previous poutcome deposit  
0    5   may      1042         1     -1         0  unknown     yes  
1    5   may      1467         1     -1         0  unknown     yes  
2    5   may      1389         1     -1         0  unknown     yes  
3    5   may       579         1     -1         0  unknown     yes  
4    5   may       673         2     -1         0  unknown     yes

## Exploratory Data Analysis (EDA)

* What is "customer attrition"?
==> Customer attrition is defined as the loss of customers by a business for whatever reason.

In [69]:
#labels
lab = df["deposit"].value_counts().keys().tolist()

#values
val = df["deposit"].value_counts().values.tolist()

trace = go.Pie(labels = lab , values = val , marker = dict(colors = [ 'red','blue'], line = dict(color = "white", width = 1.3)), rotation = 90, hoverinfo = "label+value+text", hole = .5)
layout = go.Layout(dict(title = "Customer attrition in data", plot_bgcolor = "rgb(243,243,243)", paper_bgcolor = "rgb(243,243,243)"))

data = [trace]
fig = go.Figure(data = data,layout = layout)
py.iplot(fig)
fig.show(renderer="colab")

### Varibles distribution in customer attrition

In [70]:
#function for pie plot for customer attrition types
def plot_pie(column) :
    trace1 = go.Pie(values = not_deposit[column].value_counts().values.tolist(),
                    labels = not_deposit[column].value_counts().keys().tolist(),
                    hoverinfo = "label+percent+name",
                    domain = dict(x = [0,.48]),
                    name = "Not deposit Customers",
                    marker = dict(line = dict(width = 2, color = "rgb(243,243,243)")), hole = .6)
    trace2 = go.Pie(values = deposit[column].value_counts().values.tolist(),
                    labels = deposit[column].value_counts().keys().tolist(),
                    hoverinfo = "label+percent+name",
                    marker = dict(line = dict(width = 2,color = "rgb(243,243,243)")),
                    domain = dict(x = [.52,1]),
                    hole = .6,
                    name = "Deposit customers")
    layout = go.Layout(dict(title = column + " distribution in customer attrition ",
                            plot_bgcolor = "rgb(243,243,243)",
                            paper_bgcolor = "rgb(243,243,243)",
                            annotations = [dict(text = "Not deposit customers", font = dict(size = 13), showarrow = False, x = .15, y = .5),
                                            dict(text = "deposit customers", font = dict(size = 13), showarrow = False, x = .8,y = .5)]))

    data = [trace1,trace2]
    fig = go.Figure(data = data,layout = layout)
    py.iplot(fig)
    fig.show(renderer="colab")

In [71]:
#Function for histogram for customer attrition types
def histogram(column):
    trace1 = go.Histogram(x = not_deposit[column], 
                        histnorm= "percent",
                        name = "Not deposit Customers",
                        marker = dict(line = dict(width = .5, color = "black")),
                        opacity = .9)

    trace2 = go.Histogram(x = deposit[column],
                        histnorm= "percent",
                        name = "Deposit Customers",
                        marker = dict(line = dict(width = .5, color = "black")),
                        opacity = .9)

    data = [trace1,trace2]

    layout = go.Layout(dict(title =column + " distribution in customer attrition ",
                            plot_bgcolor = "rgb(243,243,243)",
                            paper_bgcolor = "rgb(243,243,243)",
                            xaxis = dict(gridcolor = 'rgb(255, 255, 255)', title = column, zerolinewidth=1, ticklen=5, gridwidth=2),
                            yaxis = dict(gridcolor = 'rgb(255, 255, 255)',title = "percent",zerolinewidth=1,ticklen=5, gridwidth=2),
    ))

    fig = go.Figure(data=data,layout=layout)
    py.iplot(fig)
    fig.show(renderer="colab")

In [72]:
#function for scatter plot matrix for numerical columns in data
def scatter_matrix(df):
    df = df.sort_values(by = "deposit" ,ascending = True)
    classes = df["deposit"].unique().tolist()
    class_code = {classes[k] : k for k in range(2)}
    color_vals = [class_code[cl] for cl in df["deposit"]]
    pl_colorscale = "Portland"

    text = [df.loc[k,'deposit'] for k in df.index]
    text

    num_col_dimensions = [dict(label=num_col, values=df[num_col]) for num_col in num_cols]

    trace = go.Splom(dimensions = num_col_dimensions,
                    text = text,
                    marker = dict(color = color_vals, colorscale = pl_colorscale, size = 3, showscale = False, line = dict(width = .1, color='rgb(230,230,230)')))

    axis = dict(showline = True, zeroline = False, gridcolor = "#fff", ticklen = 4)

    layout = go.Layout(dict(title = "Scatter plot matrix for Numerical columns for customer attrition",
                            autosize = False,
                            height = 800,
                            width = 800,
                            dragmode = "select",
                            hovermode = "closest",
                            plot_bgcolor = 'rgba(240,240,240, 0.95)',
                            xaxis1 = dict(axis),
                            yaxis1 = dict(axis),
                            xaxis2 = dict(axis),
                            yaxis2 = dict(axis),
                            xaxis3 = dict(axis),
                            yaxis3 = dict(axis)))
    
    data = [trace]
    fig = go.Figure(data = data,layout = layout )
    py.iplot(fig)
    fig.show(renderer="colab")

In [73]:
#For all categorical columns plot pie
for i in cat_cols :
    print(i)
    plot_pie(i)

marital


education


default


housing


loan


contact


poutcome


In [74]:
#for all categorical columns plot histogram
for i in num_cols :
    histogram(i)

In [75]:
#for all numerical columns scatter plot matrix
scatter_matrix(df)

## Data Preprocessing

In [76]:
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler

In [77]:
#customer id col
Id_col = ['customerID']
df['customerID'] = df.index

In [78]:
#Target columns
target_col = ["deposit"]

In [79]:
#categorical columns
cat_cols = df.nunique()[df.nunique() < 13].keys().tolist()
cat_cols = [x for x in cat_cols if x not in target_col]

In [80]:
#numerical columns
num_cols = [x for x in df.columns if x not in cat_cols + target_col + Id_col]

#Binary columns with 2 values
bin_cols = df.nunique()[df.nunique() == 2].keys().tolist()

#Columns more than 2 values
multi_cols = [i for i in cat_cols if i not in bin_cols]

#Label encoding Binary columns
le = LabelEncoder()
for i in bin_cols :
    df[i] = le.fit_transform(df[i])

In [81]:
#Duplicating columns for multi value columns
df = pd.get_dummies(data = df,columns = multi_cols )

In [82]:
#Scaling Numerical columns
std = StandardScaler()
scaled = std.fit_transform(df[num_cols])
scaled = pd.DataFrame(scaled,columns=num_cols)

#dropping original values merging scaled values for numerical columns
df_og = df.copy()
df = df.drop(columns = num_cols,axis = 1)
df = df.merge(scaled,left_index=True,right_index=True,how = "left")
df = df.dropna()

#### Variable Summary

In [83]:
summary = (df_og[[i for i in df_og.columns if i not in Id_col]].describe().transpose().reset_index())
summary = summary.rename(columns = {"index" : "feature"})
summary = np.around(summary,3)

In [84]:
val_lst = [summary['feature'], summary['count'],
            summary['mean'],summary['std'],
            summary['min'], summary['25%'],
            summary['50%'], summary['75%'], summary['max']]

trace = go.Table(header = dict(values = summary.columns.tolist(),
                line = dict(color = ['#506784']),
                fill = dict(color = ['#119DFF'])),
                cells = dict(values = val_lst, line = dict(color = ['#506784']), fill = dict(color = ["lightgrey",'#F5F8FF'])),
                columnwidth = [200,60,100,100,60,60,80,80,80])

layout = go.Layout(dict(title = "Variable Summary"))
figure = go.Figure(data=[trace],layout=layout)
py.iplot(figure)
figure.show(renderer="colab")

### Correlation Matrix

In [85]:
#correlation
correlation = df.corr()

#tick labels
matrix_cols = df.columns.tolist()

#convert to array
corr_array = np.array(correlation)

In [86]:
#Plotting
trace = go.Heatmap(z = corr_array, x = matrix_cols, y = matrix_cols, colorscale = "Viridis",
                    colorbar = dict(title = "Pearson Correlation coefficient", titleside = "right"))

layout = go.Layout(dict(title = "Correlation Matrix for variables", autosize = False, height = 720, width = 800,
                        margin = dict(r = 0 ,l = 210, t = 25,b = 210),
                        yaxis = dict(tickfont = dict(size = 9)),
                        xaxis = dict(tickfont = dict(size = 9))))

data = [trace]
fig = go.Figure(data=data,layout=layout)
py.iplot(fig)
fig.show(renderer="colab")

### Visualising data with principal components

In [87]:
from sklearn.decomposition import PCA

In [88]:
pca = PCA(n_components = 2)
X = df[[i for i in df.columns if i not in Id_col + target_col ]]
X = X.dropna()
Y = df[target_col + Id_col]
principal_components = pca.fit_transform(X)
pca_data = pd.DataFrame(principal_components,columns = ["PC1","PC2"])
pca_data = pca_data.merge(Y,left_index=True,right_index=True,how="left")

pca_data["deposit"] = pca_data["deposit"].replace({1:"deposit",0:"not deposit"})

In [89]:
#function pca_scatter plot
def pca_scatter(target,color):
    a = pca_data[pca_data["deposit"] == target]['customerID']
    tracer = go.Scatter(x = pca_data[pca_data["deposit"] == target]["PC1"],
                        y = pca_data[pca_data["deposit"] == target]["PC2"],
                        name = target,mode = "markers",
                        marker = dict(color = color, line = dict(width = .5), symbol = "diamond-open"),
                                    text = "Customer Id : " + str(pca_data[pca_data["deposit"] == target]['customerID']))
        
    return tracer

layout = go.Layout(dict(title = "Visualising data with principal components",
                        plot_bgcolor = "rgb(243,243,243)",
                        paper_bgcolor = "rgb(243,243,243)",
                        xaxis = dict(gridcolor = 'rgb(255, 255, 255)', title = "principal component 1", zerolinewidth=1,ticklen=5,gridwidth=2),
                        yaxis = dict(gridcolor = 'rgb(255, 255, 255)',title = "principal component 2", zerolinewidth=1,ticklen=5,gridwidth=2),
                        height = 600))

trace1 = pca_scatter("deposit",'red')
trace2 = pca_scatter("not deposit",'royalblue')
data = [trace2,trace1]
fig = go.Figure(data=data,layout=layout)
py.iplot(fig)
fig.show(renderer="colab")